In [ ]:
import datetime
import pandas as pd
import numpy as np
import analytics
import math

from graphics import plot_color_map
from analytics import Swaption, BlackSwaption, BlackSwaptionVolSurface, CreditIndex, Portfolio
from analytics.scenarios import run_swaption_scenarios, run_index_scenarios, run_portfolio_scenarios, run_portfolio_scenarios_module
from scipy.interpolate import SmoothBivariateSpline
from utils.db import dbconn, dbengine
from risk.swaptions import get_swaption_portfolio
from scipy.optimize import brentq
from pandas.tseries.offsets import BDay

conn = dbconn('dawndb')
dawn_engine = dbengine('dawndb')
conn.autocommit=True
analytics.init_ontr()
pd.options.display.float_format = "{:,.2f}".format

In [ ]:
############# Current portfolio one day PNL/Delta scenario
portf = get_swaption_portfolio(datetime.date.today() - pd.offsets.BDay(), conn, source_list=['GS'])

hedges = pd.read_sql_query("SELECT security_desc, notional FROM list_cds_positions_by_strat(%s) "
                           "WHERE folder in ('IGOPTDEL', 'HYOPTDEL')",
                           conn, params=(datetime.date.today(),))

for i, r in hedges.iterrows():
    portf.add_trade(CreditIndex(r['security_desc'].split(" ")[1],
                                r['security_desc'].split(" ")[3][1:],
                                '5yr', value_date=datetime.date.today() - pd.offsets.BDay(),
                                notional = r['notional']), ('delta', i))

vol_surface = {}
for trade in portf.swaptions:
    vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                                 value_date=datetime.date.today(), interp_method = "bivariate_linear")
    vol_surface[(trade.index.index_type, trade.index.series, trade.option_type)] = vs[vs.list(source='GS', option_type=trade.option_type)[-1]]

#Set original_pv as of yesterday's EOD levels, don't reset PV after this time
portf.mark(interp_method="bivariate_linear", source_list=['GS'])
portf.reset_pv()

#set ref to today's levels
portf.value_date = datetime.date.today()
portf.mark(interp_method="bivariate_linear", source_list=['GS'])

spread_shock = np.round(np.arange(-.1, .1, .01), 4)
scens = run_portfolio_scenarios(portf, [datetime.datetime.now()], params=['pnl', 'hy_equiv'],
                                spread_shock=spread_shock,
                                vol_shock=[0],
                                corr_shock=[0],
                                vol_surface=vol_surface)
pnl = scens.xs('pnl', level = 2, axis=1).sum(axis=1)
hy_equiv = scens.xs('hy_equiv', level = 2, axis=1).sum(axis=1)

ig = CreditIndex('IG', 32, '5yr')
ig.mark()

pnl.index = pnl.index.set_levels((1+pnl.index.get_level_values('spread_shock')) * ig.spread, level = 'spread_shock')
hy_equiv.index = pnl.index

In [ ]:
pnl, hy_equiv
#plot_trade_scenarios(portf)

In [ ]:
#breakeven calc
index = 'HY'
series = 32
value_date = datetime.date.today()
option_delta = CreditIndex(index, series, '5yr')
#option_delta.spread = 56.5
option_delta.price = 106.0
option1 = BlackSwaption(option_delta, datetime.date(2019, 12, 16), 106.5, option_type="receiver") 
option1.sigma = .35
option1.notional = 100_000_000 
option_delta.notional = -option1.delta * option1.notional
portf = Portfolio([option1, option_delta], trade_ids=['opt1', 'delta'])
portf.value_date = value_date
portf.reset_pv()
portf.value_date = value_date + BDay(1)
orig_ref = portf.ref

def get_pnl(portf, x):
    portf.ref = x
    portf.sigma = float(vs[surface_id](self.T, np.log(self.moneyness)))
    return portf.pnl

if index == 'IG':
    widening = brentq(lambda x: get_pnl(portf, x), portf.ref, portf.ref + 10)
    portf.ref = orig_ref
    tightening = brentq(lambda x: get_pnl(portf, x), portf.ref-10, portf.ref)
    portf.ref = orig_ref
else: 
    widening = brentq(lambda x: get_pnl(portf, x), portf.ref-3, portf.ref)
    portf.ref = orig_ref
    tightening = brentq(lambda x: get_pnl(portf, x), portf.ref, portf.ref + 3)
    portf.ref = orig_ref

tightening, orig_ref, widening

In [ ]:
#Trade Analysis - pre-trade analytics
index = 'IG'
series = 32
option_delta = CreditIndex(index, series, '5yr') 
option_delta.spread = 55
option1 = BlackSwaption(option_delta, datetime.date(2019, 10, 16), 50, option_type="receiver") 
option2 = BlackSwaption(option_delta, datetime.date(2019, 10, 16), 77.5, option_type="payer") 
option1.sigma = .4
option2.sigma = .63
option1.notional = 100_000_000 
option2.notional = 100_000_000 
option1.direction = 'Long' 
option2.direction = 'Short' 
option_delta.notional = -option1.delta * option1.notional - option2.delta * option2.notional
portf = Portfolio([option1, option2, option_delta], trade_ids=['opt1', 'opt2', 'delta'])

In [ ]:
date_range = pd.bdate_range(portf.value_date, portf.value_date + pd.tseries.offsets.BDay(30), freq='3B')
vol_shock = np.arange(-.15, .31, 0.01)
spread_shock = np.arange(-.2, 2, 0.01)
vol_surface = {}
for trade in portf.swaptions:
    vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                             value_date=portf.value_date, interp_method = "bivariate_linear")
    vol_surface[(trade.index.index_type, trade.index.series, trade.option_type)] = vs[vs.list(source='GS', option_type=trade.option_type)[-1]]

df = run_portfolio_scenarios(portf, date_range, params=["pnl"],
                             spread_shock = spread_shock,
                             vol_shock = vol_shock,
                             vol_surface = vol_surface)
df = df.reset_index()
df.vol_shock = df.vol_shock.round(2)

In [ ]:
def plot_trade_scenarios(portf, shock_min=-.15, shock_max=.2, vol_time_roll=True):
    portf.reset_pv()
    end_date = min(portf.swaptions, key=lambda x: x.exercise_date).exercise_date
    date_range = pd.bdate_range(portf.value_date,
                                end_date - pd.tseries.offsets.BDay(), freq='3B')
    vol_shock = np.arange(-.15, .31, 0.01)
    spread_shock = np.arange(shock_min, shock_max, 0.01)
    index = portf.indices[0].index_type
    vol_surface = {}
    for trade in portf.swaptions:
        vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                                 value_date=portf.value_date, interp_method = "bivariate_linear")
        vol_surface[(trade.index.index_type, trade.index.series, trade.option_type)] = vs[vs.list(option_type=trade.option_type)[-1]]
    
    df = run_portfolio_scenarios(portf, date_range, params=["pnl","delta"],
                                 spread_shock = spread_shock,
                                 vol_shock = vol_shock,
                                 vol_surface = vol_surface)
    df = df.reset_index()
    df.vol_shock = df.vol_shock.round(2)

    if index == 'HY':
        df['price'] = 100 + (500 - portf.indices[0].spread * (1 + df.spread_shock)) \
                    * abs(portf.indices[0].DV01) / portf.indices[0].notional * 100
        df = df.set_index(['date', 'price', 'vol_shock'])
        sort_order = [True, False]
    else:
        df['spread'] = portf.indices[0].spread * (1 +  df.spread_shock)
        df = df.set_index(['date', 'spread', 'vol_shock'])
        sort_order = [True, False]
    
    #If the multilevels index contains strategy drop it
    if df.columns.nlevels == 3: 
        df.columns = df.columns.droplevel(level=0)
    pnl = df.xs('pnl', axis=1, level=1).sum(axis=1)
    for trade_id, t in portf.items():
        if isinstance(t, BlackSwaption):
            if len(trade_id) == 2:
                trade_id = trade_id[1]
            df[(trade_id, 'delta')] *= -t.notional 
    delta = df.xs('delta', axis=1, level=1).sum(axis=1).xs(0, level='vol_shock')
    delta += sum([x.notional * -1 if x.direction == 'Buyer' else 1 for x in portf.indices])

    pnl.name = 'pnl'
    delta.name = 'delta'

    plot_color_map(pnl.xs(0, level='vol_shock'), sort_order)
    plot_color_map(delta, sort_order)
    plot_color_map(pnl.loc[date_range[-1]], sort_order)

In [ ]:
def calc_simple_scenario(portf, shock_min=-.15, shock_max=.2):
    portf.reset_pv()
    end_date = min(portf.swaptions, key=lambda x: x.exercise_date).exercise_date
    date_range = pd.bdate_range(portf.value_date,
                                end_date - pd.tseries.offsets.BDay(), freq='3B')
    vol_shock = [0]
    spread_shock = np.arange(shock_min, shock_max, 0.01)
    index = portf.indices[0].index_type
    vol_surface = {}
    for trade in portf.swaptions:
        vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                                 value_date=portf.value_date, interp_method = "bivariate_linear")
        vol_surface[(trade.index.index_type, trade.index.series, trade.option_type)] = vs[vs.list(option_type=trade.option_type)[-1]]

    df = run_portfolio_scenarios(portf, date_range, params=["pnl"],
                                 spread_shock = spread_shock,
                                 vol_shock = vol_shock,
                                 vol_surface = vol_surface)

    return df.xs('pnl', axis=1, level=1).sum(axis=1) 

In [ ]:
#Dec Jan 2017 Trade
option_delta = CreditIndex.from_tradeid(864)
option1 = BlackSwaption.from_tradeid(3, option_delta)
option2 = BlackSwaption.from_tradeid(4, option_delta)
portf = Portfolio([option1, option2, option_delta], trade_ids=['opt1', 'opt2', 'delta'])
#plot_trade_scenarios(portf)

#Feb 2017: Sell May Buy April Calendar Trade
option_delta = CreditIndex.from_tradeid(870)
option1 = BlackSwaption.from_tradeid(5, option_delta)
option2 = BlackSwaption.from_tradeid(6, option_delta)
portf = Portfolio([option1, option2, option_delta], trade_ids=['opt1', 'opt2', 'delta'])
#plot_trade_scenarios(portf)

#April 2017: Sell May Buy June Calendar Trade
option_delta = CreditIndex.from_tradeid(874)
option1 = BlackSwaption.from_tradeid(7, option_delta)
option2 = BlackSwaption.from_tradeid(8, option_delta)
portf = Portfolio([option1, option2, option_delta], trade_ids=['opt1', 'opt2', 'delta'])
#plot_trade_scenarios(portf)

#June July 2017 Calendar Trade
option_delta_pf = CreditIndex.from_tradeid(874)
option_delta2_pf = CreditIndex.from_tradeid(879)

option1_pf = BlackSwaption.from_tradeid(7, option_delta_pf)
option2_pf = BlackSwaption.from_tradeid(9, option_delta_pf)
option_delta_pf.notional = 50_335_169

portf = Portfolio([option1_pf, option2_pf, option_delta_pf], trade_ids=['opt1', 'opt2', 'delta'])
portf.value_date = datetime.date(2017, 5, 17)
portf.mark()
#plot_trade_scenarios(portf)

#July 2017: Buy Sept HY payer spread
option_delta = CreditIndex.from_tradeid(891)
option1 = BlackSwaption.from_tradeid(10, option_delta)
option2 = BlackSwaption.from_tradeid(11, option_delta)
portf = Portfolio([option1, option2, option_delta], trade_ids=['opt1', 'opt2', 'delta'])
#plot_trade_scenarios(portf)

#March 2019: May Bull Risky
option_delta = CreditIndex.from_tradeid(1063)
option1 = BlackSwaption.from_tradeid(41, option_delta)
option2 = BlackSwaption.from_tradeid(40, option_delta)
portf = Portfolio([option1, option2, option_delta], trade_ids=['opt1', 'opt2', 'delta'])
results = calc_simple_scenario(portf, shock_min=-.3, shock_max=.3)

In [ ]:
#Look at steepness of volatility - 30 days, .85 vs .15 payer deltas on HY
days = 30
delta1 = .85
delta2 = .15
index = 'HY'

sql_str = "select b.quotedate, b.ref, b.ref_id, b.expiry, a.delta_pay, a.vol from " \
          "swaption_quotes a join swaption_ref_quotes b on a.ref_id = b.ref_id and index = %s"
df = pd.read_sql_query(sql_str, dbengine('serenitasdb'), 
     index_col=['quotedate'], parse_dates={'quotedate': {'utc': True}}, params=[index])
df['days_expiry'] =  (df.expiry - df.index.date).dt.days
r_1 = []
for i, g in df.groupby(pd.Grouper(freq='D', level='quotedate')):
    r = []
    for i_1, g_1 in g.groupby(['days_expiry', 'delta_pay']):
        r.append([i_1[0], i_1[1], g_1['vol'].mean()])
    if len(r) > 0:
        temp = np.dstack(r)
        f = SmoothBivariateSpline(temp[0][0], temp[0][1], temp[0][2])
        r = (f(days, delta1) - f(days, delta2))[0][0]
        r_1.append([i, r])
    else:
        pass
df_1 = pd.DataFrame(r_1, columns=['date', 'steepness'])
df_1.set_index('date').plot()